In [1]:
import finnhub_utils
import alpha_vantage_utils
import llm_utils
import candle_utils
import json
import report_generation
import pandas as pd


news = alpha_vantage_utils.AlphaVantageClient(debug=True).get_news('META', days_back=100, prefilter=False)
#transcripts, markdown_transcript = alpha_vantage_utils.AlphaVantageClient().get_earnings_from('COIN', 2020)


#llm_utils.call_openai('COIN', markdown_transcript)

#alpha_vantage_utils.AlphaVantageClient().get_news('COIN')

In [2]:

import format_utils
format_utils.set_pandas_format()
news

ticker_sentiment_score  relevance_score  \
0                  0.123318         0.116914   
1                  0.536045         0.781806   
2                  0.397416         0.251032   
3                  0.247281         0.114956   
4                  0.048135         0.060694   
5                  0.153113         0.049526   
6                  0.251684         0.146025   
7                  0.390886         0.457566   
8                  0.000000         0.050572   
9                  0.000000         0.043264   
10                 0.000000         0.022410   
11                 0.117942         0.111488   
12                 0.269574         0.223350   
13                -0.005092         0.073434   
14                 0.000000         0.046907   
15                 0.000000         0.050044   
16                 0.338855         0.102668   
17                 0.180892         0.163539   
18                 0.022241         0.025985   
19                 0.156504         0.038468   
20                 0.062078         0.027603   
21                 0.268339         0.127007   
22                 0.148205         0.064449   
23                -0.008015         0.043818   
24                -0.024027         0.066598   
25                 0.000000         0.049732   
26                -0.011861         0.153470   
27                 0.134551         0.121650   
28                 0.126336         0.107978   
29                 0.145794         0.142989   
30                 0.048187         0.161710   
31                 0.527696         0.593175   
32                 0.242138         0.045396   
33                 0.000000         0.131643   
34                 0.000000         0.131643   
35                 0.186486         0.243701   
36                -0.137001         0.059341   
37                 0.000000         0.056943   
38                 0.000000         0.058188   
39                 0.000000         0.057907   
40                 0.000000         0.059049   
41                 0.325281         0.217639   
42                 0.112052         0.305690   
43                 0.000000         0.059488   
44                 0.000000         0.061315   
45                 0.000000         0.057215   
46                 0.000000         0.056943   
47                 0.000000         0.085629   
48                 0.000000         0.081276   
49                 0.000000         0.059194   
50                 0.111023         0.162802   
51                 0.000000         0.059785   
52                 0.137724         0.108958   
53                 0.073181         0.057215   
54                 0.257471         0.174167   
55                 0.000000         0.057490   
56                 0.000000         0.068896   
57                 0.000000         0.060541   
58                -0.189921         0.073659   
59                 0.167008         0.057352   
60                 0.454800         0.351060   
61                 0.108880         0.049424   
62                 0.000000         0.066047   
63                 0.000000         0.070517   
64                 0.189336         0.131284   
65                 0.525213         0.188193   
66                 0.076999         0.055364   
67                 0.098274         0.013662   
68                 0.000000         0.035929   
69                 0.000000         0.070310   
70                 0.000000         0.056674   
71                 0.000000         0.044141   
72                 0.000000         0.067347   
73                -0.380317         0.631880   
74                 0.000000         0.079392   
75                 0.000000         0.053035   
76                 0.095721         0.110717   
77                 0.186796         0.189175   
78                 0.116045         0.035875   
79                 0.179726         0.067919   
80                 0.255466         0.063091   
81                 0.066593         0.043264   
82                 0.

In [16]:
news_list = []
symbol = 'NVDA'
fields= ['title', 'url',
  'time_published', 
  'summary', 
  'source', 'category_within_source',
    'source_domain', 
    #'topics',
     'overall_sentiment_score', 'overall_sentiment_label'
     ]
for feed in news['feed']:
    for ts in feed['ticker_sentiment']:
        if ts['ticker'] == symbol:
            data = [float(ts['ticker_sentiment_score']), float(ts['relevance_score'])]
            for f in fields:
                data.append(feed[f])
            news_list.append(data)

df_news = pd.DataFrame.from_records(news_list, columns=['ticker_sentiment_score', 'relevance_score']+fields)

In [21]:
df_news.query('relevance_score>0.5').query("source!='Motley Fool' and source != 'Benzinga' and source !='Zacks Commentary'" )

ticker_sentiment_score  relevance_score  \
78                 0.250776         0.546745   
98                 0.040731         0.654522   
137                0.031246         0.580434   
138               -0.191123         0.856646   
147               -0.105290         0.975103   
611                0.552651         0.551622   
620                0.552651         0.551622   
672                0.550599         0.712594   

                                                                                                                   title  \
78                                        'How can we trust you?': China's state media urges Nvidia to prove chip safety   
98                              Nvidia denies back-door features in its H20 chips after Beijing raises security concerns   
137                        Nvidia's China-bound H20 AI chips face Beijing scrutiny over 'tracking' and security concerns   
138                                         Breaking | China summons Nvidia to explain H20 chips 'back door' safety risk   
147                                                     NVIDIA Sets Conference Call for Second-Quarter Financial Results   
611  WeRide Teams Up With Lenovo to Launch 100% Automotive-Grade HPC 3.0 Platform Powered by NVIDIA DRIVE AGX Thor Chips   
620  WeRide Teams Up With Lenovo to Launch 100% Automotive-Grade HPC 3.0 Platform Powered by NVIDIA DRIVE AGX Thor Chips   
672                                           Nvidia CEO Jensen Huang sells an additional $12.94 million worth of shares   

                                                                                                                                                                                            url  \
78                                                                https://www.scmp.com/tech/tech-war/article/3320500/how-can-we-trust-you-chinas-state-media-calls-nvidia-prove-safety-h20-chip   
98                                                     https://www.scmp.com/tech/tech-war/article/3320382/nvidia-denies-back-door-features-its-h20-chips-after-beijing-raises-security-concerns   
137                                                                                                       https://www.cnbc.com/2025/07/31/china-probes-nvidia-h20-chips-for-tracking-risks.html   
138                                                     https://www.scmp.com/tech/tech-war/article/3320240/chinas-cyberspace-regulator-summons-nvidia-explain-h20-chips-alleged-back-door-risks   
147                                                    https://www.globenewswire.com/news-release/2025/07/30/3124527/0/en/NVIDIA-Sets-Conference-Call-for-Second-Quarter-Financial-Results.html   
611  https://www.globenewswire.com/news-release/2025/07/21/3118796/0/en/WeRide-Teams-Up-With-Lenovo-to-Launch-100-Automotive-Grade-HPC-3-0-Platform-Powered-by-NVIDIA-DRIVE-AGX-Thor-Chips.html   
620  https://www.globenewswire.com/news-release/2025/07/21/3118651/0/en/WeRide-Teams-Up-With-Lenovo-to-Launch-100-Automotive-Grade-HPC-3-0-Platform-Powered-by-NVIDIA-DRIVE-AGX-Thor-Chips.html   
672                                                                                                                   https://www.cnbc.com/2025/07/19/nvidia-ceo-jensen-huang-sells-shares.html   

      time_published  \
78   20250801T141421   
98   20250801T053053   
137  20250731T061842   
138  20250731T051749   
147  20250730T210000   
611  20250721T132200   
620  20250721T115800   
672  20250719T170210   

                                                                                                                                                                                                                                                                                                          summary  \
78   A People's Daily opinion piece urged Nvidia Corp to prove the safety of its products a day after the US semiconductor giant denied the existence of alleged back-door fe

In [1]:
import yfinance as yf

ticker = yf.Ticker("AAPL")  # Replace with your stock symbol

# Get financials
income_stmt = ticker.financials
balance_sheet = ticker.balance_sheet

# For margins:
gross_margin = income_stmt.loc['Gross Profit'] / income_stmt.loc['Total Revenue']
operating_margin = income_stmt.loc['Operating Income'] / income_stmt.loc['Total Revenue']
net_margin = income_stmt.loc['Net Income'] / income_stmt.loc['Total Revenue']

print("Gross Margin:\n", gross_margin)
print("Operating Margin:\n", operating_margin)
print("Net Margin:\n", net_margin)


Gross Margin:
 2024-09-30    0.462063
2023-09-30    0.441311
2022-09-30    0.433096
2021-09-30    0.417794
2020-09-30         NaN
dtype: object
Operating Margin:
 2024-09-30    0.315102
2023-09-30    0.298214
2022-09-30    0.302887
2021-09-30    0.297824
2020-09-30         NaN
dtype: object
Net Margin:
 2024-09-30    0.239713
2023-09-30    0.253062
2022-09-30    0.253096
2021-09-30    0.258818
2020-09-30         NaN
dtype: object


In [2]:
# ROIC ≈ NOPAT / Invested Capital
# Approximate NOPAT: Net Income * (1 - Tax Rate)
# Approximate Invested Capital: Total Assets - Current Liabilities - Cash

tax_rate = 0.21  # Use actual if known
net_income = income_stmt.loc['Net Income']
nopat = net_income * (1 - tax_rate)

total_assets = balance_sheet.loc['Total Assets']
current_liab = balance_sheet.loc['Current Liabilities']
cash = balance_sheet.loc['Cash']
invested_capital = total_assets - current_liab - cash

roic = nopat / invested_capital
print("ROIC:\n", roic)


KeyError: 'Cash'

In [3]:
balance_sheet

2024-09-30  \
Treasury Shares Number                                       NaN   
Ordinary Shares Number                             15116786000.0   
Share Issued                                       15116786000.0   
Net Debt                                           76686000000.0   
Total Debt                                        106629000000.0   
...                                                          ...   
Cash Cash Equivalents And Short Term Investments   65171000000.0   
Other Short Term Investments                       35228000000.0   
Cash And Cash Equivalents                          29943000000.0   
Cash Equivalents                                    2744000000.0   
Cash Financial                                     27199000000.0   

                                                      2023-09-30  \
Treasury Shares Number                                       0.0   
Ordinary Shares Number                             15550061000.0   
Share Issued                                       15550061000.0   
Net Debt                                           81123000000.0   
Total Debt                                        111088000000.0   
...                                                          ...   
Cash Cash Equivalents And Short Term Investments   61555000000.0   
Other Short Term Investments                       31590000000.0   
Cash And Cash Equivalents                          29965000000.0   
Cash Equivalents                                    1606000000.0   
Cash Financial                                     28359000000.0   

                                                      2022-09-30  \
Treasury Shares Number                                       NaN   
Ordinary Shares Number                             15943425000.0   
Share Issued                                       15943425000.0   
Net Debt                                           96423000000.0   
Total Debt                                        132480000000.0   
...                                                          ...   
Cash Cash Equivalents And Short Term Investments   48304000000.0   
Other Short Term Investments                       24658000000.0   
Cash And Cash Equivalents                          23646000000.0   
Cash Equivalents                                    5100000000.0   
Cash Financial                                     18546000000.0   

                                                      2021-09-30 2020-09-30  
Treasury Shares Number                                       NaN        NaN  
Ordinary Shares Number                             16426786000.0        NaN  
Share Issued                                       16426786000.0        NaN  
Net Debt                                           89779000000.0        NaN  
Total Debt                                        136522000000.0        NaN  
...                                                          ...        ...  
Cash Cash Equivalents And Short Term Investments   62639000000.0        NaN  
Other Short Term Investments                       27699000000.0        NaN  
Cash And Cash Equivalents                          34940000000.0        NaN  
Cash Equivalents                                   17635000000.0        NaN  
Cash Financial                                     17305000000.0        NaN  

[68 rows x 5 columns]

In [ ]:
from IPython.display import Markdown, display

display(Markdown(markdown_transcript))

In [2]:
response = llm_utils.call_openai('COIN', markdown_transcript)
response

[{'type': 'input_text', 'text': 'Based on the following analysis, create a Cathie Wood-style investment signal.\n            Analysis Data for COIN:\n            ### 📄 **COIN 2025Q2 Earnings Conference Call**\n\n👤 **Operator** _(Sentiment: 0.0)_\n> Good afternoon. My name is Kate, and I will be your conference operator today. I would like to welcome everyone to the Coinbase Second Quarter 2025 Earnings Call. Anil Gupta, Vice President of Investor Relations, you may begin your conference.\n\n👤 **Anil K. Gupta** _(Sentiment: 0.0)_\n> Good afternoon, and welcome to the Coinbase second quarter 2025 earnings call. Joining me on today\'s call are Brian Armstrong, Co-Founder and CEO; Emilie Choi, President and COO; Alesia Haas, CFO; and Paul Grewal, Chief Legal Officer. I hope you\'ve all had the opportunity to read our Shareholder Letter, which was published earlier today on our Investor Relations website. During today\'s call, we may make forward-looking statements, which may vary materiall

'{"signal":"bullish","confidence":75,"reasoning":"Coinbase delivered record growth in the quarter, with MTUs rising 415% YoY to 11.4 million and trading volume up 8.5× YoY. Subscription & services revenue grew 169% YoY, tempering reliance on trading fees. The company achieved $1.1 billion in adjusted EBITDA, has a $5.6 billion cash and stablecoin cushion plus $483 million in crypto investments, and no exposure to recent credit events. Product momentum is strong across staking (1 million+ users), launch of Coinbase NFT, Prime brokerage expansion, USDC payments, and Base L2. Active policy engagement and global licensing further de-risk growth. While volatility remains, Coinbase’s financial strength, diversified revenue streams, and strategic investments support long-term upside."}'

In [3]:
len(markdown_transcript)

713469

In [ ]:
import finnhub_utils
import format_utils
import format_utils
df = finnhub_utils.get_earnings_and_profiles('2025-07-31','amc', stock_limit =200)



In [3]:
format_utils.show_formatted(df.query('change_after_earning>0.1'))

date symbol ticker                        shortName  \
32   2025-07-31    BIO    BIO       Bio-Rad Laboratories, Inc.   
28   2025-07-31   BFAM   BFAM  Bright Horizons Family Solution   
106  2025-07-31   IRTC   IRTC       iRhythm Technologies, Inc.   
189  2025-07-31     WK     WK                     Workiva Inc.   
20   2025-07-31   ATEC   ATEC          Alphatec Holdings, Inc.   
54   2025-07-31    CPS    CPS    Cooper-Standard Holdings Inc.   

                   industry change_after_earning change_after_earning_cc  \
32          Medical Devices               11.98%                  17.63%   
28        Personal Services               12.62%                  10.61%   
106         Medical Devices               11.61%                  17.68%   
189  Software - Application               16.56%                  32.07%   
20          Medical Devices               13.23%                  30.15%   
54               Auto Parts               18.55%                   9.29%   

    epsActual epsEstimate eps_diff_percent revenueActual revenueEstimate  \
32       2.61        1.75           32.92%        651.6M          621.4M   
28       1.07        1.03            3.68%        731.6M          738.8M   
106   -32.00%     -48.55%          -51.72%        186.7M          177.4M   
189    19.00%       5.64%           70.32%        215.2M          215.2M   
20      2.00%     -19.21%            10.60        185.5M          182.4M   
54      6.00%      -5.66%             1.94        706.0M          693.9M   

    revenue_diff_percent    beta revenuePerShare revenueGrowth  \
32                 4.64%  94.90%           91.96         2.10%   
28                -0.99%    1.30           48.42         9.20%   
106                4.96%     NaN           20.83        26.10%   
189                0.02%  86.40%           14.44        21.20%   
20                 1.71%     NaN            4.67        27.50%   
54                 1.71%    2.80          153.57        -0.30%   

    priceToSalesTrailing12Months priceToBook priceEpsCurrentYear  \
32                          2.96        1.08               29.50   
28                          2.57        5.12               29.49   
106                         8.06       51.09             -118.02   
189                         5.85      -70.78               63.19   
20                          2.99       86.06               -1.8K   
54                        17.00%       -4.76              -48.19   

    fiftyDayAverage profitMargins trailingEps forwardEps totalRevenue  \
32           240.51        12.50%       11.10      11.65         2.6B   
28           120.96         6.34%        3.05       4.08         2.8B   
106          142.55       -14.06%       -3.13      -1.84       657.2M   
189           67.80        -8.25%       -1.19       1.31       807.0M   
20            11.43       -24.33%       -1.13    -65.00%       682.2M   
54            22.75         1.08%        1.69     75.00%         2.7B   

    marketCapitalization  
32                  7.6B  
28                  7.2B  
106                 5.3B  
189                 4.7B  
20                  2.0B  
54                462.2M

In [10]:
import pandas as pd
def show_formatted(dataframe):
    df_display = dataframe.copy()
    string_names = []
    numeric_names = []
    for col in df_display.columns:
        if col not in ['symbol','ticker','industry', 'shortName', 'date']:
            df_display[col] = pd.to_numeric(df_display[col], errors='coerce')
            df_display[col] = df_display[col].apply(format_utils.format_large_numbers)
            numeric_names.append(col)
        else:
            string_names.append(col)
    return df_display[string_names+numeric_names]


df2 = show_formatted(df)
df2

date symbol ticker                        shortName  \
0  2025-07-31   AAPL   AAPL                       Apple Inc.   
2  2025-07-31   AMZN   AMZN                 Amazon.com, Inc.   
8  2025-07-31     MA     MA          Mastercard Incorporated   
1  2025-07-31   ABBV   ABBV                      AbbVie Inc.   
5  2025-07-31  CMCSA  CMCSA              Comcast Corporation   
3  2025-07-31    BMY    BMY     Bristol-Myers Squibb Company   
6  2025-07-31    CVS    CVS           CVS Health Corporation   
4  2025-07-31     CI     CI                  The Cigna Group   
9  2025-07-31    WKC    WKC         World Kinect Corporation   
7  2025-07-31   HEPS   HEPS  D-Market Electronic Services &    

                         industry epsActual epsEstimate eps_diff_percent  \
0            Consumer Electronics      1.57        1.46            6.84%   
2                 Internet Retail      1.68        1.36           19.30%   
8                 Credit Services      4.15        4.15            0.08%   
1    Drug Manufacturers - General      2.97        2.94            0.94%   
5                Telecom Services      1.25        1.22            2.75%   
3    Drug Manufacturers - General      1.46        1.08           25.95%   
6                Healthcare Plans      1.81        1.47           18.69%   
4                Healthcare Plans      7.20        7.37           -2.34%   
9  Oil & Gas Refining & Marketing    59.00%      48.82%           17.25%   
7                 Internet Retail     -2.44         NaN              NaN   

  change_after_earning revenueActual revenueEstimate revenue_diff_percent  \
0                1.59%         94.0B           91.3B                2.88%   
2               -7.22%        167.7B          165.3B                1.42%   
8               -0.46%          8.1B            8.2B               -0.87%   
1                0.48%         15.4B           15.3B                0.63%   
5                0.36%         30.3B           30.7B               -1.29%   
3                0.69%         12.3B           11.5B                6.36%   
6                0.35%         98.9B           95.4B                3.51%   
4                0.79%         67.1B           64.3B                4.17%   
9               -1.72%          9.0B            9.4B               -4.14%   
7                0.37%         17.5B             NaN                  NaN   

     beta revenuePerShare revenueGrowth priceToSalesTrailing12Months  \
0    1.20           27.17         9.60%                         7.35   
2    1.34           63.37        13.30%                         3.42   
8    1.02           33.07        16.80%                        16.74   
1  48.10%           32.97         6.60%                         5.91   
5  94.70%           32.76         2.10%                       96.69%   
3  37.10%           23.49         0.60%                         1.89   
6  57.60%          304.54         8.40%                       20.62%   
4  45.40%          961.02        11.00%                       26.71%   
9    1.36          676.22       -17.50%                        3.62%   
7     NaN          173.73        65.60%                        1.45%   

  priceToBook priceEpsCurrentYear fiftyDayAverage profitMargins trailingEps  \
0       45.67               27.40          205.28        24.30%        6.60   
2        6.86               32.68          217.61        10.54%        6.55   
8       64.59               34.38          565.33        44.93%       14.84   
1      242.81               16.31          188.18         6.45%        2.11   
5        1.24                7.57           34.79        18.44%        6.03   
3        5.18                6.80           47.50        10.58%        2.49   
6        1.02               10.05           64.31         1.18%        3.59   
4        1.74                8.84          309.00         1.92%       18.25   
9      87.66%               11.10           28.13        -1.11%       -7.51   
7      25.35%               -1.18   

In [11]:
df2.dtypes

date                            object
symbol                          object
ticker                          object
shortName                       object
industry                        object
epsActual                       object
epsEstimate                     object
eps_diff_percent                object
change_after_earning            object
revenueActual                   object
revenueEstimate                 object
revenue_diff_percent            object
beta                            object
revenuePerShare                 object
revenueGrowth                   object
priceToSalesTrailing12Months    object
priceToBook                     object
priceEpsCurrentYear             object
fiftyDayAverage                 object
profitMargins                   object
trailingEps                     object
forwardEps                      object
totalRevenue                    object
marketCapitalization            object
dtype: object

In [7]:
df.columns

Index(['date', 'symbol', 'ticker', 'shortName', 'industry', 'epsActual',
       'epsEstimate', 'eps_diff_percent', 'change_after_earning',
       'revenueActual', 'revenueEstimate', 'revenue_diff_percent', 'beta',
       'revenuePerShare', 'revenueGrowth', 'priceToSalesTrailing12Months',
       'priceToBook', 'priceEpsCurrentYear', 'fiftyDayAverage',
       'profitMargins', 'trailingEps', 'forwardEps', 'totalRevenue',
       'marketCapitalization'],
      dtype='object')

In [4]:
type(df.iloc[0].priceToSalesTrailing12Months)

float

In [7]:
import yfinance as yf
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)
# sometimes it doesn't work.
pd.option_context('display.float_format', '{:,.2f}'.format, 
                    'display.precision', 2)
pd.set_option('display.max_seq_items', None)  # For lists/arrays
info = yf.Ticker('MSFT').info

In [3]:
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_seq_items', None)  # For lists/arrays
df

Date Ticker       Close        High         Low        Open  \
0  2025-07-31   AAPL  207.570007  209.839996  207.160004  208.490005   
1  2025-07-31   ABBV  189.020004  198.830002  187.619995  197.059998   
2  2025-07-31    AEE  101.129997  101.239998   99.120003   99.480003   
3  2025-07-31    AES   12.973999   13.062795   12.796409   12.924669   
4  2025-07-31   AGCO  117.970001  121.160004  111.870003  116.250000   
5  2025-07-31    AJG  287.250000  290.929993  281.829987  282.019989   
6  2025-07-31   AMZN  234.110001  236.529999  231.399994  235.770004   
7  2025-07-31    APD  287.880005  296.510010  285.989990  292.540009   
8  2025-07-31   APTV   68.639999   69.790001   66.400002   68.230003   
9  2025-07-31    ARW  116.000000  130.639999  115.879997  126.620003   
10 2025-07-31    BAX   21.760000   24.160000   21.469999   23.760000   
11 2025-07-31   BIIB  128.000000  135.429993  127.239998  133.000000   
12 2025-07-31    BIP   31.200001   31.400000   30.150000   30.809999   
13 2025-07-31   BLDR  127.129997  127.809998  118.169998  121.940002   
14 2025-07-31    BMY   43.310001   45.509998   42.959999   44.169998   
15 2025-07-31    BWA   36.799999   37.049999   35.040001   36.049999   
16 2025-07-31     CI  267.380005  297.500000  264.220001  293.190002   
17 2025-07-31  CMCSA   33.230000   34.099998   32.900002   33.990002   
18 2025-07-31    CVS   62.099998   66.919998   61.230000   65.510002   
19 2025-07-31   DINO   43.939999   44.680000   43.340000   44.169998   
20 2025-07-31    DXC   13.610000   13.830000   13.480000   13.660000   
21 2025-07-31    EIX   52.119999   52.279999   51.009998   51.540001   
22 2025-07-31    EME  627.489990  667.640015  616.039978  667.640015   
23 2025-07-31    EMN   72.610001   73.370003   72.070000   72.730003   
24 2025-07-31     ES   66.099998   66.300003   65.510002   65.510002   
25 2025-07-31    EXC   44.939999   44.970001   43.900002   43.950001   
26 2025-07-31   HEPS    2.690000    2.690000    2.530000    2.570000   
27 2025-07-31    HII  278.859985  293.140015  277.570007  278.670013   
28 2025-07-31    ICE  184.830002  187.380005  182.699997  185.740005   
29 2025-07-31     IP   46.740002   52.279999   46.639999   51.040001   
30 2025-07-31   KLAC  879.030029  897.190002  860.000000  864.450012   
31 2025-07-31    LNC   38.110001   38.189999   35.529999   35.750000   
32 2025-07-31   LPLA  395.730011  403.579987  392.380005  400.000000   
33 2025-07-31   LUMN    4.450000    4.520000    4.390000    4.470000   
34 2025-07-31     MA  566.469971  579.440002  562.510010  568.570007   
35 2025-07-31    MTZ  189.210007  194.000000  188.309998  190.559998   
36 2025-07-31   NCLH   25.559999   27.100000   25.170000   26.120001   
37 2025-07-31   PARA   12.570000   12.610000   11.540000   12.000000   
38 2025-07-31    PBF   22.600000   24.870001   22.360001   23.500000   
39 2025-07-31    PCG   14.020000   14.080000   13.320000   13.880000   
40 2025-07-31    PWR  406.130005  423.500000  399.070007  406.089996   
41 2025-07-31    RGA  192.449997  193.850006  189.470001  189.470001   
42 2025-07-31     SO   94.480003   95.900002   92.910004   94.879997   
43 2025-07-31   SPGI  551.099976  558.859985  532.380005  535.130005   
44 2025-07-31    SYK  392.730011  401.989990  392.070007  398.269989   
45 2025-07-31    WCC  206.960007  212.940002  200.000000  200.000000   
46 2025-07-31    WKC   27.270000   27.770000   26.930000   27.510000   
47 2025-07-31    WTW  315.809998  320.179993  302.000000  307.559998   
48 2025-07-31    XEL   73.440002   73.870003   72.669998   72.900002   
49 2025-07-31    XYL  144.619995  144.830002  135.000000  137.710007   

       Volume     Date_1     Close_1      High_1       Low_1      Open_1  \
0    80698400 2025-08-01  202.380005  213.580002  201.500000  210.869995   
1    10347900 2025-08-01  195.220001  197.059998  189.789993  189.919998   
2     2002100 2025-08-01  102.110001  103.169998  100.379997  102.540001   
3    15200000 2025-08-01   13.23

In [150]:
model='gpt-4.1'
response = llm_utils.call_openai_with_transcript(transcript=markdown_transcript, 
                                      model=model,
                                      query="Given those quarterly earnings transcript, summarize CRDO company trends and highlights over years."
                                      "How does the management team do? Do they keep their goal consistent and reach goal set previously?"
                                      "Do they change any of their operating plan?")

In [2]:
model='gpt-4.1'
response = llm_utils.call_openai_with_transcript(transcript=markdown_transcript, 
                                      model=model,
                                      query=llm_utils.MULTI_EARNINGS_CALL_SUMMARY_PROMPT)

In [151]:
len(markdown_transcript)


449152

In [ ]:
from IPython.display import Markdown, display

display(Markdown(response))

# get multiple earnings call and ask LLM to summary

In [ ]:

#fcx = finnhub_utils.get_sec_filing('FCX')
model='gpt-4.1'

for symbol in ['CTSH']:
    alpha_vantage_client = alpha_vantage_utils.AlphaVantageClient()
    earnings = alpha_vantage_client.get_earnings_call(symbol)
    if len(earnings['transcript']) > 0:
        print(f'{symbol}earnings call: {len(earnings['transcript'])}')
        candle_utils.save_ticker_1y_candle(symbol)
        img_path = f'./imgs/{symbol}_candle.png'
        transcript_response = llm_utils.call_openai_with_transcript(transcript=json.dumps(earnings), model=model)
        candle_response=llm_utils.call_openai_with_image_path(img_path, model)
        llm_response=llm_utils.call_openai_with_img_transcript(img_path, json.dumps(earnings), model)
        report_generation.generate_report({symbol: [transcript_response, candle_response, llm_response]})
        break

In [ ]:
transcript_response = llm_utils.call_openai_with_transcript(transcript=json.dumps(earnings))
candle_response=llm_utils.call_openai_with_image_path(f'./imgs/{symbol}_candle.png')

# get earnings data from finnhub

# get sec filing raw data

In [24]:
import requests

url = "https://www.sec.gov/Archives/edgar/data/320193/000032019323000106/aapl-20230930.htm"
headers = {
    "User-Agent": "MyApp/1.0 (myemail@example.com)",
    "Accept-Encoding": "gzip, deflate",
    "Host": "www.sec.gov"
}

response = requests.get(url, headers=headers)
html_text = response.text
print(response)

<Response [200]>


In [29]:
print(response.content)

b'<?xml version="1.0" ?><!--XBRL Document Created with the Workiva Platform--><!--Copyright 2023 Workiva--><!--r:c68c2fd8-345e-4faa-8610-8b173d5da094,g:843081e3-ad04-4f75-a78c-e87ea3423788,d:1cb1ba018cb1455aa66bd3f9ab0c5b1a--><html xmlns:ix="http://www.xbrl.org/2013/inlineXBRL" xmlns:dei="http://xbrl.sec.gov/dei/2023" xmlns:ixt="http://www.xbrl.org/inlineXBRL/transformation/2020-02-12" xmlns:ixt-sec="http://www.sec.gov/inlineXBRL/transformation/2015-08-31" xmlns:aapl="http://www.apple.com/20230930" xmlns="http://www.w3.org/1999/xhtml" xmlns:link="http://www.xbrl.org/2003/linkbase" xmlns:srt="http://fasb.org/srt/2023" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:country="http://xbrl.sec.gov/country/2023" xmlns:us-gaap="http://fasb.org/us-gaap/2023" xmlns:iso4217="http://www.xbrl.org/2003/iso4217" xmlns:xbrli="http://www.xbrl.org/2003/instance" xmlns:xbrldi="http://xbrl.org/2006/xbrldi" xmlns:ecd="http://xbrl.sec.gov/ecd/2023" xml

'\n\naapl-20230930\nfalse\n2023\nFY\n0000320193\nP1Y\n67\nP1Y\n25\nP1Y\n7\n1\nhttp://fasb.org/us-gaap/2023#MarketableSecuritiesCurrent http://fasb.org/us-gaap/2023#MarketableSecuritiesNoncurrent\nhttp://fasb.org/us-gaap/2023#MarketableSecuritiesCurrent http://fasb.org/us-gaap/2023#MarketableSecuritiesNoncurrent\nhttp://fasb.org/us-gaap/2023#LongTermDebtCurrent http://fasb.org/us-gaap/2023#LongTermDebtNoncurrent\nhttp://fasb.org/us-gaap/2023#LongTermDebtCurrent http://fasb.org/us-gaap/2023#LongTermDebtNoncurrent\nhttp://fasb.org/us-gaap/2023#OtherAssetsNoncurrent\nhttp://fasb.org/us-gaap/2023#OtherAssetsNoncurrent\nhttp://fasb.org/us-gaap/2023#PropertyPlantAndEquipmentNet\nhttp://fasb.org/us-gaap/2023#PropertyPlantAndEquipmentNet\nhttp://fasb.org/us-gaap/2023#OtherLiabilitiesCurrent\nhttp://fasb.org/us-gaap/2023#OtherLiabilitiesCurrent\nhttp://fasb.org/us-gaap/2023#OtherLiabilitiesNoncurrent\nhttp://fasb.org/us-gaap/2023#OtherLiabilitiesNoncurrent\nhttp://fasb.org/us-gaap/2023#OtherLiab

In [28]:

# Parse with lxml HTML parser
from lxml import etree, html

tree = html.fromstring(response.content)

# Extract all visible text (including inside ix: tags)
# This will include iXBRL tagged content
ix_texts = tree.xpath('//ix:nonnumeric | //ix:nonfraction')

# Extract text content
all_text = []
for ix in ix_texts:
    # Get either the text inside the tag or fallback to .text_content()
    txt = ix.text_content().strip()
    if txt:
        all_text.append(txt)

# Combine into a full document string
document_text = "\n".join(all_text)

print(document_text[:2000])  # preview

XPathEvalError: Undefined namespace prefix

In [16]:
sec_filings.query('type=="10-K"').edgarUrl.iloc[0]



'https://finance.yahoo.com/sec-filing/AAPL/0000320193-23-000106_320193'